In [1]:
import time
%matplotlib inline
import numpy as np
import pandas as pd
import seaborn as sns
from sklearn import metrics
import matplotlib.pyplot as plt
from mpl_toolkits import mplot3d
from sklearn.utils import shuffle
from sklearn.decomposition import PCA
from sklearn.pipeline import make_pipeline
from sklearn.tree import DecisionTreeClassifier
from sklearn.impute import KNNImputer, SimpleImputer
from sklearn.feature_selection import RFECV, SelectFromModel, RFE
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.compose import make_column_selector, make_column_transformer
from sklearn.preprocessing import StandardScaler,RobustScaler,OrdinalEncoder, LabelEncoder
from sklearn.ensemble import IsolationForest, GradientBoostingClassifier, RandomForestClassifier, ExtraTreesClassifier
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay, classification_report, f1_score
from sklearn.linear_model import SGDClassifier, RidgeClassifier, Perceptron, PassiveAggressiveClassifier
from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score, StratifiedKFold,RandomizedSearchCV
from tpot import TPOTClassifier
from sklearn import tree
import lime, shap
from lime import lime_tabular
from IPython.display import HTML
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import BernoulliNB

In [2]:
df = pd.read_csv('C:/Users/Admin/Desktop/stage emmanuel/datasets/datasets avec classe autre/data_cervus.csv')
df = df.rename(columns = {'Unnamed: 0': 'label'})
df = df.fillna(0)


In [3]:
n = len(df.index)
x = 0
while x < n:
    a = 'cerf' in df.iloc[x,0]
    b = 'daim' in df.iloc[x,0]
    c = 'meagC' in df.iloc[x,0]
    if a == True :
        df.iloc[x,0] = 'cerf'
    elif b == True :
        df.iloc[x,0] = 'daim'
        
    elif c == True :
        df.iloc[x,0] = 'meagC'
    else:
        df.iloc[x,0] = 'Autre' 
    x = x+1       

In [4]:
df['label'], uniques = pd.factorize(df['label']) # on appel une autre variale afin d'y inclure l'Index
y = df['label']
X = df.drop('label', axis=1)
X = X.apply(lambda x: x/x.max(), axis=1)  # pour base de données normalisé par le maximum de la ligne

In [5]:
X, y = shuffle(X, y, random_state=0)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=0, stratify=y)

In [6]:
cv=StratifiedKFold(n_splits=10, shuffle=True, random_state=0)

In [7]:
sgd=SGDClassifier()
logreg=LogisticRegression()
ridge=RidgeClassifier()
perceptron=Perceptron()
pasag=PassiveAggressiveClassifier()
#tree=DecisionTreeClassifier()
models=[sgd,logreg,ridge,perceptron,pasag]

In [8]:
models

[SGDClassifier(),
 LogisticRegression(),
 RidgeClassifier(),
 Perceptron(),
 PassiveAggressiveClassifier()]

In [9]:
for model in models:
    model.fit(X_train,y_train)
    print(model.score(X_test,y_test))

0.9354838709677419
0.9032258064516129
0.967741935483871
0.967741935483871
0.967741935483871


In [10]:
shap.initjs()

In [11]:
i=1
liste_exp=[]
for model in models:
    try:
        lin_reg_explainer = shap.LinearExplainer(model, X_train)
        liste_exp.append(lin_reg_explainer)
    except Exception:
        tree_explainer = shap.explainers.Tree(model, X_train)
        liste_exp.append(tree_explainer)
for model_exp, model in zip(liste_exp,models):
    for i in range(len(X_test)):
        shap_vals = model_exp.shap_values(np.array(X_test)[i])
        print(shap_vals)#pour chaque observation , retourne les valeurs de shap associées a chaque features
        print("Base Value : ", model_exp.expected_value)
        print(f"True type: {np.array(y_test)[i]}")
        print(f"Prediction From Model {model}: ", model.predict(np.array(X_test)[i].reshape(1,-1))[0])
        print("Prediction From Adding SHAP Values to Base Value : ", model_exp.expected_value + np.array(shap_vals).sum())

[array([ 9.07119547e-04,  3.47683387e-04,  7.65293163e-06,  1.70747847e-04,
       -1.20383017e-05, -2.36238062e-04,  1.08590314e-05, -1.28268478e-03,
        4.88343249e-06, -5.15667273e-03, -6.89103064e-04, -6.54687235e-03,
       -5.13619132e-04, -4.54690460e-03,  8.28464182e-06,  5.38339343e-04,
       -1.46431401e-03, -1.06600940e-02, -1.91890323e-02,  2.05444812e-05,
       -2.97327273e-03,  3.17980650e-04,  1.92804742e-02, -5.45007484e-03,
        1.01294679e-03, -1.02837414e-03,  1.39630386e-04, -1.51995433e-04,
       -1.41727888e-03, -2.77266120e-04,  1.82171827e-05, -1.07331843e-04,
        5.06765502e-04,  6.34898746e-06, -3.01867969e-04,  3.95633866e-04,
       -3.82944982e-04,  1.88902448e-05,  3.02948401e-03,  3.54150738e-04,
       -1.08053052e-04,  3.10318747e-04, -3.10772166e-03, -2.35170293e-05,
        1.56823233e-05,  3.28825525e-03, -3.46376149e-05, -1.45238710e-03,
       -6.71291598e-03,  8.06617118e-06,  1.56029739e-04,  1.49436462e-04,
        2.49341135e-04, 

X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names


[array([ 9.07119547e-04,  3.47683387e-04,  7.65293163e-06,  1.70747847e-04,
       -1.20383017e-05, -2.36238062e-04,  1.08590314e-05, -1.28268478e-03,
        4.88343249e-06, -2.52628011e-03, -6.89103064e-04, -6.54687235e-03,
       -5.13619132e-04, -4.54690460e-03,  8.28464182e-06,  5.38339343e-04,
       -1.46431401e-03, -1.06600940e-02, -8.35691943e-03,  2.05444812e-05,
       -2.97327273e-03,  3.17980650e-04,  8.98242158e-03, -4.79577543e-02,
        1.01294679e-03, -1.02837414e-03, -3.89386586e-04, -1.51995433e-04,
       -1.41727888e-03, -2.77266120e-04,  1.82171827e-05, -1.07331843e-04,
        5.06765502e-04,  6.34898746e-06, -3.01867969e-04,  3.95633866e-04,
       -3.82944982e-04,  1.88902448e-05,  3.02948401e-03,  3.54150738e-04,
       -1.08053052e-04,  3.10318747e-04, -3.11905589e-03, -2.35170293e-05,
        1.56823233e-05,  3.28825525e-03, -3.46376149e-05, -1.45238710e-03,
       -6.55214312e-04, -6.05086222e-05,  1.56029739e-04,  1.49436462e-04,
        2.49341135e-04, 

X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted with feature names
X does not have valid feature names, but SGDClassifier was fitted

Prediction From Model SGDClassifier():  0
Prediction From Adding SHAP Values to Base Value :  [-36.02195029 -63.94485917 -81.10506011 -82.82064575]
[array([ 9.07119547e-04,  3.47683387e-04,  7.65293163e-06,  1.70747847e-04,
       -1.20383017e-05, -2.36238062e-04,  1.08590314e-05, -1.28268478e-03,
        4.88343249e-06, -1.63850132e-02, -6.89103064e-04, -6.54687235e-03,
       -5.13619132e-04, -4.54690460e-03,  8.28464182e-06,  5.38339343e-04,
       -1.46431401e-03, -1.06600940e-02,  7.50926502e-03,  2.05444812e-05,
       -2.97327273e-03,  3.17980650e-04, -1.67114646e-02,  8.63702046e-02,
        1.01294679e-03, -1.02837414e-03,  1.39630386e-04, -1.51995433e-04,
        9.94789117e-03, -2.77266120e-04,  1.82171827e-05, -1.07331843e-04,
        5.06765502e-04,  6.34898746e-06, -3.01867969e-04,  3.95633866e-04,
       -3.82944982e-04,  1.88902448e-05,  3.02948401e-03, -4.87752480e-03,
       -1.08053052e-04,  3.10318747e-04,  4.53861862e-04, -2.35170293e-05,
        1.56823233e-05,  3

...

X does not have valid feature names, but Perceptron was fitted with feature names
X does not have valid feature names, but Perceptron was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names


Prediction From Model PassiveAggressiveClassifier():  0
Prediction From Adding SHAP Values to Base Value :  [ 0.07310259 -3.35350221 -3.39689957 -3.21528745]
[array([ 7.20876912e-05,  2.41025891e-05,  7.48926009e-05,  2.69491109e-05,
        2.37274826e-07, -2.06494846e-05, -4.48513688e-06, -3.88437310e-04,
        7.61161377e-07, -4.51748849e-03, -3.36596620e-05, -6.37137821e-04,
        1.06720390e-07, -8.49696945e-04, -5.64661659e-06, -1.65018029e-05,
       -5.18740306e-05, -1.44311675e-03, -3.82748126e-04, -6.67232635e-05,
       -3.72920152e-04, -8.09929254e-06, -6.15310034e-03, -6.22161911e-03,
       -1.74700442e-04, -3.28044307e-05, -1.02963305e-04, -3.31365346e-05,
       -1.50348176e-04, -1.55307229e-04,  4.26064253e-05, -4.49834996e-05,
        4.51387792e-05, -7.21725843e-06,  5.09653224e-04,  3.52369377e-05,
       -8.39570166e-05,  5.75307386e-07, -1.68161158e-04,  4.02107636e-05,
        2.21667146e-05, -7.03946512e-05,  5.50027424e-05,  2.73702764e-05,
        2.191200

X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names


[array([ 7.20876912e-05,  2.41025891e-05,  7.48926009e-05,  2.69491109e-05,
        2.37274826e-07, -2.06494846e-05, -4.48513688e-06, -3.88437310e-04,
        7.61161377e-07, -1.33638218e-04, -3.36596620e-05, -6.37137821e-04,
        1.55555030e-06, -8.49696945e-04, -5.64661659e-06, -7.52012468e-06,
       -5.18740306e-05, -3.31877175e-04, -2.88883845e-04,  2.90873231e-06,
       -3.72920152e-04, -8.09929254e-06,  2.27173292e-03, -3.82252853e-03,
        2.06289811e-04, -3.28044307e-05,  2.04051987e-05, -3.31365346e-05,
       -1.50348176e-04, -1.55307229e-04, -4.99413941e-06, -4.49834996e-05,
        4.51387792e-05, -7.21725843e-06, -7.46852621e-05, -7.13217154e-05,
        5.03922002e-05,  5.75307386e-07, -7.67978582e-05,  4.02107636e-05,
        2.21667146e-05,  2.47031668e-05,  5.50027424e-05, -1.01178111e-05,
        2.19120094e-06,  2.73564155e-04, -3.04744782e-04, -3.72906831e-05,
       -7.77124314e-05,  2.16276393e-06,  1.69315669e-05,  2.17102377e-05,
       -1.58567703e-04, 

X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
X does not have valid feature names, but PassiveAggressiveClassifier was fitted with feature names
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limi

In [12]:
plt.rcParams['figure.figsize'] = (5,10)

In [13]:
help(shap.bar_plot)

Help on function bar_legacy in module shap.plots._bar:

bar_legacy(shap_values, features=None, feature_names=None, max_display=None, show=True)



In [14]:
for model_exp in liste_exp:
    for i in range(len(X_test)):
        shap.bar_plot(model_exp.shap_values(np.array(X_test)[i]), feature_names=X_test.columns, max_display=len(X_test.columns))

TypeError: only integer scalar arrays can be converted to a scalar index

In [ ]:
for model_exp in liste_exp:
    for i in range(len(X_test)):
        shap_vals = model_exp.shap_values(np.array(X_test)[i])
        shap.force_plot(model_exp.expected_value, shap_vals, feature_names=X_test.columns, out_names="Type Patient",matplotlib=True)

In [ ]:
for model in models:
    explainer = shap.Explainer(model,X_train)
    shap_values = explainer(X_train)
    shap.plots.bar(shap_values, max_display=12)